In [ ]:
dataset_name = "CSTR"

# Imports, load data , training functions and database creation

## Imports

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
time: 1.76 s (started: 2024-09-09 23:29:06 +00:00)


In [ ]:
!pip install ipython-autotime
%load_ext autotime

  Using cached jedi-0.19.1-py2.py3-none-any.whl.metadata (22 kB)
Using cached jedi-0.19.1-py2.py3-none-any.whl (1.6 MB)
time: 309 µs (started: 2024-09-09 23:26:10 +00:00)


In [ ]:
import pandas as pd
import numpy as np
import matplotlib as plt
import os, errno
import shutil
import networkx as nx
from networkx.algorithms import bipartite
import json
import yaml
import ast
from sklearn.metrics import classification_report
from sklearn.neighbors import NearestNeighbors
import pickle
import time

import tensorflow as tf

time: 13.3 s (started: 2024-09-09 23:26:10 +00:00)


In [ ]:
import torch

os.environ['TORCH'] = torch.__version__
print(torch.__version__)

!pip install -q torch-scatter -f https://data.pyg.org/whl/torch-${TORCH}.html
!pip install -q torch-sparse -f https://data.pyg.org/whl/torch-${TORCH}.html
!pip install -q git+https://github.com/pyg-team/pytorch_geometric.git

2.4.0+cu121
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.9/10.9 MB 30.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.1/5.1 MB 31.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
time: 38.7 s (started: 2024-09-09 23:26:23 +00:00)


In [ ]:
import torch_geometric
import torch.nn.functional as F
import torch_geometric.transforms as T
from torch_geometric.utils.convert import from_networkx
from torch_geometric.nn import SAGEConv, GATConv, Linear, to_hetero
from torch_geometric.data import HeteroData

time: 4.19 s (started: 2024-09-09 23:27:02 +00:00)


In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

time: 10.6 ms (started: 2024-09-09 23:27:06 +00:00)


In [ ]:
!pip install -U sentence-transformers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 6.2 MB/s eta 0:00:00
time: 4.65 s (started: 2024-09-09 23:27:06 +00:00)


In [ ]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-MiniLM-L6-v2')

/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

time: 9.06 s (started: 2024-09-09 23:27:11 +00:00)


In [ ]:
# Move the model to GPU
if torch.cuda.is_available():
    device = torch.device('cuda')
    model.to(device)

time: 5.3 ms (started: 2024-09-09 23:27:20 +00:00)


In [ ]:
print(model.device.type)

cuda
time: 9 ms (started: 2024-09-09 23:27:20 +00:00)


## Load scoring Database

In [ ]:
# # Only execude if dafaframes do not exist YET

# df_list = []

# for i in range(10):
#     aux_list = []

#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # acuracia
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # precision
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # recall
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # f1-score
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # support
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # time
#     aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30'])) # coarse
#     # aux_list.append(pd.DataFrame(columns = ['1','5','10','20','30','80']))

#     df_list.append(aux_list)

#     try:
#         os.makedirs("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i))
#     except OSError as e:
#         if e.errno != errno.EEXIST:
#             raise

#     # df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
#     # df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
#     # df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
#     # df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
#     # df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
#     df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # time
#     df_list[i][6].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_coarse.pkl") # coarsening node and edges

time: 265 µs (started: 2024-09-09 23:27:20 +00:00)


In [ ]:
df_list = []
for i in range(10):
    aux_list = []
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl")) # acuracia
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl")) # precision
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl")) # recall
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl"))  # f1-score
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl")) # support
    aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl")) # time
    #aux_list.append(pd.read_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_coarse.pkl")) # coarsening node and edges
    df_list.append(aux_list)

time: 20.1 s (started: 2024-09-09 23:27:20 +00:00)


In [ ]:
df_list[0][0]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.180572  0.393195  0.446724  0.489474   
Dmoz_Computers_keyphrase2_GAT    0.263685  0.427007  0.479377  0.530044   
Dmoz_Computers_keyphrase3_GCN    0.235524  0.436151  0.481633  0.541338   
Dmoz_Computers_keyphrase3_GAT    0.244489  0.456034  0.499033  0.567544   
Dmoz_Computers_keyphrase23_GCN   0.200506   0.42488  0.495811  0.545285   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT    0.10971  0.192075  0.264229  0.400956   
Industry_Sector_keyphrase3_GCN   0.126178  0.143885  0.246637  0.236446   
Industry_Sector_keyphrase3_GAT   0.108007  0.208176  0.338278  0.397575   
Industry_Sector_keyphrase23_GCN  0.117547  0.174832   0.22732  0.306168   
Industry_Sector_keyphrase23_GAT  0.055196  0.209889  0.320225   0.42066   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN     0.51299  NaN  0.480526  
Dmoz_Computers_keyphrase2_GAT    0.540202  NaN  0.520526  
Dmoz_Computers_keyphrase3_GCN     0.54009  NaN  0.388947  
Dmoz_Computers_keyphrase3_GAT    0.569317  NaN  0.424737  
Dmoz_Computers_keyphrase23_GCN   0.556215  NaN  0.148947  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.272674  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.170864  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.410666  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.370344  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.418233  NaN       NaN  

[72 rows x 7 columns]

time: 81.2 ms (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
df_list[0][5]

1          5         10         20  \
Industry_Sector_keyphrase2_GCN   5.967893  14.137134  19.774683   7.163521   
Industry_Sector_keyphrase2_GAT   2.891018   5.089645   4.946186   6.673805   
Industry_Sector_keyphrase3_GCN   5.692917  13.041445  21.713131  16.310932   
Industry_Sector_keyphrase3_GAT   2.746514   4.288752   5.765436   6.155356   
Industry_Sector_keyphrase23_GCN  4.684616  13.329979  20.220493  26.668284   
...                                   ...        ...        ...        ...   
re8_keyphrase3_GAT               1.624291   2.651562   2.304905   3.118137   
re8_keyphrase23_GCN              3.228727   8.169865   2.386437   4.594121   
re8_keyphrase23_GAT              1.617132   2.309624   2.679503   2.871684   
CSTR_keyphrase2_GCN              0.777569   0.405382   0.457566   0.517418   
CSTR_keyphrase2_GAT              0.361262   0.349818   0.271651   0.351861   

                                       30  
Industry_Sector_keyphrase2_GCN   4.032328  
Industry_Sector_keyphrase2_GAT   5.501309  
Industry_Sector_keyphrase3_GCN   6.837297  
Industry_Sector_keyphrase3_GAT   7.282659  
Industry_Sector_keyphrase23_GCN  39.06455  
...                                   ...  
re8_keyphrase3_GAT               3.377965  
re8_keyphrase23_GCN              8.840206  
re8_keyphrase23_GAT              3.079119  
CSTR_keyphrase2_GCN                   NaN  
CSTR_keyphrase2_GAT                   NaN  

[68 rows x 5 columns]

time: 45 ms (started: 2024-09-09 23:27:40 +00:00)


# Functions

## Count function

In [ ]:
def count_ED(path,model_name):
    with open(path) as f:
        data = json.load(f)
        df_list[iteration][6].at[model_name+"_source_vertices_D", str(rotulated)] = data["source_vertices"][0]
        df_list[iteration][6].at[model_name+"_source_vertices_E", str(rotulated)] = data["source_vertices"][1]
        df_list[iteration][6].at[model_name+"_source_vcount", str(rotulated)] = data["source_vcount"]
        df_list[iteration][6].at[model_name+"_source_ecount", str(rotulated)] = data["source_ecount"]
        df_list[iteration][6].at[model_name+"_vertices_D", str(rotulated)] = data["vertices"][0]
        df_list[iteration][6].at[model_name+"_vertices_E", str(rotulated)] = data["vertices"][1]
        df_list[iteration][6].at[model_name+"_vcount", str(rotulated)] = data["vcount"]
        df_list[iteration][6].at[model_name+"_ecount", str(rotulated)] = data["ecount"]

time: 9.12 ms (started: 2024-09-09 23:27:40 +00:00)


## Embedding functions

In [ ]:
def get_nodes(model_name,rotulated,iteration):
    # carregamento de nós do grafo
    with open('/content/drive/MyDrive/mestrado_v2/processed_datasets/'+dataset_name+'/'+keyphrase+'/graph.pkl','rb') as f:
        aux =  pickle.load(f)
        document_nodes_text,context_nodes_text = aux[0],aux[1]

    # Aqui realizamos a junção dos textos dos nodes agrupados
    node_groups=[]
    with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+model_name+"_"+str(rotulated)+'_'+str(iteration)+".source") as f:
        for line in f:
            node_groups.append([int(x) for x in line.strip().split(' ')])

    number_doc_nodes = len(document_nodes_text)

    new_document_nodes_text = []
    new_context_nodes_text = []

    doc_coarsened_nodes = []
    context_coarsened_nodes = []

    cont_separacao_dc = 0

    # iterate over coarsened node groups
    for node_group in node_groups:
        # Testing if node is a document or a context
        if node_group[0] < number_doc_nodes:
            combined_text = ''
            # for each document composing this node concatenate their text
            for node in node_group:
                if combined_text == '':
                    combined_text = document_nodes_text[node]
                else:
                    combined_text = combined_text + ' ' +  document_nodes_text[node]
            new_document_nodes_text.append(combined_text)
            # Determinamos um ponte de separacao entre documento e contextos
            cont_separacao_dc += 1
            # vetor com todos os gupos de documentos
            doc_coarsened_nodes.append(node_group)
        else:
            combined_text = ''
            # for each context composing this node concatenate their text
            for node in node_group:
                if combined_text == '':
                    combined_text = context_nodes_text[node-len(document_nodes_text)]
                else:
                    combined_text = combined_text + ' ' +  context_nodes_text[node-len(document_nodes_text)]
            new_context_nodes_text.append(combined_text)
            # vetor com todos os gupos de contextos
            context_coarsened_nodes.append(node_group)

    return new_document_nodes_text, new_context_nodes_text

time: 1.53 ms (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
# save embeddings
# def create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text):
#     with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/document_nodes_embeddings"+str(rotulated)+'_'+str(iteration), 'wb') as handle:
#         pickle.dump(model.encode(new_document_nodes_text, show_progress_bar=True, device=device, convert_to_tensor = True), handle)

#     with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/context_nodes_embeddings"+str(rotulated)+'_'+str(iteration), 'wb') as handle:
#         pickle.dump(model.encode(new_context_nodes_text, show_progress_bar=True, device=device, convert_to_tensor = True), handle)

time: 255 µs (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text):
    document_nodes_embeddings = model.encode(new_document_nodes_text, show_progress_bar=True, device=device, convert_to_tensor = True)

    context_nodes_embeddings = model.encode(new_context_nodes_text, show_progress_bar=True, device=device, convert_to_tensor = True)

    return document_nodes_embeddings,context_nodes_embeddings

time: 497 µs (started: 2024-09-09 23:27:40 +00:00)


## Graph definition functions

In [ ]:
def get_edges(model_name,rotulated,iteration,doc_coarsened_nodes,context_coarsened_nodes,cont_separation):
    # Loading eges creted by the corsening algorithm
    coarcening_edges=[]
    with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+model_name+"_"+str(rotulated)+'_'+str(iteration)+".ncol") as f:
        for line in f:
            coarcening_edges.append([int(x) for x in line.strip().split(' ')])

    # re-ading excluded edges for later reading them to the graph
    with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/exc_edges_"+model_name+"_"+str(rotulated)+'_'+str(iteration), 'rb') as handle:
        exc_edges = pickle.load(handle)

    # ajusta o formato das egdes retiram a coluna de pesos
    coarcening_edges = np.array(coarcening_edges)
    coarcening_edges = np.delete(coarcening_edges, 2, 1)

    # temos que incluir as arestas excluidas anteriormente:

    # Cria um dicionario capaz de saber qual nó corresponde a cada nó de um agrupamento de documentos e contextos que sofreram coarsening
    doc_not_coarsened_to_coarsened = {}
    for i,doc_nodes in enumerate(doc_coarsened_nodes):
        for doc in doc_nodes:
            doc_not_coarsened_to_coarsened[doc] = i

    contx_not_coarsened_to_coarsened = {}
    for i,contx_nodes in enumerate(context_coarsened_nodes):
        for doc in contx_nodes:
            contx_not_coarsened_to_coarsened[doc] = i

    # concatena com arestas excluidas anteriormente
    for exc_edg in exc_edges:
        coarcening_edges = np.concatenate((coarcening_edges, np.array([[doc_not_coarsened_to_coarsened[exc_edg[0]],contx_not_coarsened_to_coarsened[exc_edg[1]]+len(doc_coarsened_nodes)]])), axis=0)

    # Ajusta eges para transpostas e valores
    coarcening_edges = coarcening_edges.T
    coarcening_edges[1] = coarcening_edges[1] - len(doc_coarsened_nodes)

    coarcening_edges = torch.tensor(coarcening_edges)

    return coarcening_edges

time: 1.29 ms (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def generate_mask(train_mask,doc_coarsened_nodes):
    quant_train_mask = train_mask.long().sum()
    new_train_mask = [False for i in range(len(doc_coarsened_nodes))] # 5520

    new_val_mask = torch.tensor(new_train_mask)

    for i in range(quant_train_mask):
        new_train_mask[i] = True

    new_train_mask= torch.tensor(new_train_mask)
    new_test_mask = torch.logical_not(new_train_mask)

    return [new_train_mask, new_val_mask, new_test_mask]

time: 693 µs (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def generate_y(y,train_mask,doc_coarsened_nodes):
    # Cria um dicionario capaz de saber qual nó corresponde a cada  nó de um agrupamento de cdocumentos
    coarsened_to_not_coarsened = {}
    not_coarsened_to_coarsened = {}
    for i,doc_nodes in enumerate(doc_coarsened_nodes):
        coarsened_to_not_coarsened[i] = doc_nodes
        for doc in doc_nodes:
            not_coarsened_to_coarsened[doc] = i

    # Cria um dicionaria que relaciona coarsened Y e not coarsened Y
    new_y_dict = {}
    for i in range(len(doc_coarsened_nodes)):
        new_y_dict[i] = []

    for i,label in enumerate(y.numpy()):
        new_y_dict[not_coarsened_to_coarsened[i]].append(label)

    # Lista de Y falsos do tamanho do grafo
    fake_y =[]
    quant_train_mask = train_mask.long().sum()

    for i in range(len(doc_coarsened_nodes)):
        if i < quant_train_mask:
            fake_y.append(new_y_dict[i][0])
        else:
            fake_y.append(0)

    fake_y = np.array(fake_y)
    fake_y = torch.tensor(fake_y)
    fake_y = fake_y.type(torch.LongTensor)

    return fake_y,new_y_dict,coarsened_to_not_coarsened

time: 900 µs (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def get_doc_coarsened_nodes(rotulated,iteration,document_nodes_text):
    # Aqui realizamos a junção dos textos dos nodes agrupados
    node_groups=[]
    with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+model_name+"_"+str(rotulated)+'_'+str(iteration)+".source") as f:
        for line in f:
            node_groups.append([int(x) for x in line.strip().split(' ')])

    number_doc_nodes = len(document_nodes_text)

    doc_coarsened_nodes = []
    context_coarsened_nodes = []

    cont_separation = 0

    # iterate over coarsened node groups
    for node_group in node_groups:
        # Testing if node is a document or a context
        if node_group[0] < number_doc_nodes:
            # Determinamos um ponte de separacao entre documento e contextos
            cont_separation += 1
            # vetor com todos os gupos de documentos
            doc_coarsened_nodes.append(node_group)
        else:
            # vetor com todos os gupos de contextos
            context_coarsened_nodes.append(node_group)

    return doc_coarsened_nodes,context_coarsened_nodes,cont_separation

time: 845 µs (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def set_up_graph(model_name,rotulated,iteration,new_document_nodes_embeddings, new_context_nodes_embeddings):
    # carregamento de nós do grafo
    with open('/content/drive/MyDrive/mestrado_v2/processed_datasets/'+dataset_name+'/'+keyphrase+'/graph.pkl','rb') as f:
        aux =  pickle.load(f)
        document_nodes_text, y, class_number, classes = aux[0], aux[2], aux[3], aux[4]

    # carrega mascaras antigas
    if rotulated==80:
        with open('/content/drive/MyDrive/Mestrado_Grafos/processed_datasets/'+dataset_name+'/masks/mask_rot'+str(rotulated)+'%_'+str(iteration)+'.pkl', 'rb') as f:
            aux = pickle.load(f)
            old_train_mask = aux[0]
    else:
        with open('/content/drive/MyDrive/Mestrado_Grafos/processed_datasets/'+dataset_name+'/masks/mask_rot'+str(rotulated)+'_'+str(iteration)+'.pkl', 'rb') as f:
            aux = pickle.load(f)
            old_train_mask = aux[0]

    # # Carrega embeddings de documentos
    # new_document_nodes_embeddings=[]
    # with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/document_nodes_embeddings"+str(rotulated)+'_'+str(iteration), 'rb') as handle:
    #     try:
    #         while True:
    #             data = pickle.load(handle)
    #             new_document_nodes_embeddings.append(data)
    #     except EOFError:
    #         pass

    # # Carrega embeddings de contextos
    # new_context_nodes_embeddings=[]
    # with open("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/context_nodes_embeddings"+str(rotulated)+'_'+str(iteration), 'rb') as handle:
    #     try:
    #         while True:
    #             data = pickle.load(handle)
    #             new_context_nodes_embeddings.append(data)
    #     except EOFError:
    #         pass

    # carrega nodes com coarsening
    doc_coarsened_nodes,context_coarsened_nodes,cont_separation = get_doc_coarsened_nodes(rotulated,iteration,document_nodes_text)

    coarcening_edges = get_edges(model_name,rotulated,iteration,doc_coarsened_nodes,context_coarsened_nodes,cont_separation)

    new_train_mask, new_val_mask, new_test_mask = generate_mask(old_train_mask,doc_coarsened_nodes)

    fake_y, real_y_dict, coarsened_to_not_coarsened = generate_y(y,old_train_mask,doc_coarsened_nodes)

    # Define objeto do grafo
    data = HeteroData()
    # nodes
    # data['document'].x = new_document_nodes_embeddings[0]
    data['document'].x = new_document_nodes_embeddings
    # data['concept'].x = new_context_nodes_embeddings[0]
    data['concept'].x = new_context_nodes_embeddings
    # edges
    data['document', 'has', 'concept'].edge_index = coarcening_edges
    #class labels
    data['document'].y = fake_y
    # Setting graph to undirected
    data = T.ToUndirected()(data)
    # Remove duplicate edges
    data = T.RemoveDuplicatedEdges()(data)
    # Ensure date in using gpu
    data = data.to(device)
    # print
    print(data)

    return data, real_y_dict, new_train_mask, new_val_mask, new_test_mask,coarsened_to_not_coarsened, class_number, classes

time: 1.39 ms (started: 2024-09-09 23:27:40 +00:00)


## Training functions and Model Definitions

### Training

In [ ]:
def train(model,optimizer):
    model.train()
    optimizer.zero_grad()
    out = model(data.x_dict, data.edge_index_dict)
    mask = data['document'].train_mask
    loss = F.cross_entropy(out['document'][mask], data['document'].y[mask])
    loss.backward()
    optimizer.step()
    return float(loss)

time: 647 µs (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def test(model,real_y_values,coarsened_to_not_coarsened):
    model.eval()
    out = model(data.x_dict, data.edge_index_dict)
    # Devemos redimencionar as predicoes
    pred = out['document'].argmax(dim=1)

    real_y = [item for dit in real_y_values for item in dit]
    real_y = torch.tensor(real_y)

    real_pred = []
    for i in range(len(pred)):
        for j in range(len(coarsened_to_not_coarsened[i])):
            real_pred.append(pred[i])
    real_pred = torch.tensor(real_pred).cpu()

    # Extend the list by appending the last value repeated
    repeated_t = data['document'].train_mask[-1].repeat((len(real_pred)-len(data['document'].train_mask)))
    extended_train_mask = torch.cat((data['document'].train_mask,repeated_t), dim=0)

    repeated_t = data['document'].test_mask[-1].repeat((len(real_pred)-len(data['document'].test_mask)))
    extended_test_mask = torch.cat((data['document'].test_mask,repeated_t), dim=0)

    accs = []
    for mask in [extended_train_mask, extended_test_mask]:
        accs.append(int((real_pred[mask] == real_y[mask]).sum()) / int(mask.sum()))
    return accs

time: 1.23 ms (started: 2024-09-09 23:27:40 +00:00)


In [ ]:
def get_y(model,real_y_values,coarsened_to_not_coarsened):
    model.eval()
    out = model(data.x_dict, data.edge_index_dict)
    pred = out['document'].argmax(dim=1)

    real_y = [item for dit in real_y_values for item in dit]
    real_y = torch.tensor(real_y)

    real_pred = []
    for i in range(len(pred)):
        for j in range(len(coarsened_to_not_coarsened[i])):
            real_pred.append(pred[i])
    real_pred = torch.tensor(real_pred).cpu()

    # Extend the list by appending the last value repeated
    repeated_t = data['document'].test_mask[-1].repeat((len(real_pred)-len(data['document'].test_mask)))
    extended_test_mask = torch.cat((data['document'].test_mask,repeated_t), dim=0)

    print("PREDICTIONS ->", pred)

    # y_pred, y_true
    return real_pred[extended_test_mask],real_y[extended_test_mask]

time: 947 µs (started: 2024-09-09 23:27:40 +00:00)


### GNN Model

In [ ]:
# First Network
from torch_geometric.nn import GraphConv

class GNN(torch.nn.Module):
    def __init__(self, hidden_channels, out_channels):
        super().__init__()
        self.conv1 = GraphConv(-1, hidden_channels)
        self.conv2 = GraphConv(-1, out_channels)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index).relu()
        x = self.conv2(x, edge_index)
        return x

time: 761 µs (started: 2024-09-09 23:27:40 +00:00)


### GAT Model

In [ ]:
# Second Network
from torch_geometric.nn import GATv2Conv

class GAT(torch.nn.Module):
    def __init__(self, hidden_channels, out_channels):
        super().__init__()
        self.conv1 = GATv2Conv((-1, -1), hidden_channels, add_self_loops=False)
        self.lin1 = Linear(-1, hidden_channels)
        self.conv2 = GATv2Conv((-1, -1), out_channels, add_self_loops=False)
        self.lin2 = Linear(-1, out_channels)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index) + self.lin1(x)
        x = x.relu()
        x = self.conv2(x, edge_index) + self.lin2(x)
        return x

time: 2.68 ms (started: 2024-09-09 23:27:40 +00:00)


### iteration

In [ ]:
def training_iteration(i, rotulated, GCN_or_GAT, data, real_y_dict, new_train_mask, new_val_mask, new_test_mask,coarsened_to_not_coarsened,class_number,classes):
    # Define classes
    class_number = class_number
    target_names = classes

    # for i in range(10):
    print(f"\n===============================================")
    print(f"================ {GCN_or_GAT} - MODEL {i} ================")
    print(f"===============================================\n")

    # Defining masks
    data['document'].train_mask = new_train_mask
    data['document'].val_mask = new_val_mask
    data['document'].test_mask = new_test_mask

    # Generate MODEL and Optmizer
    if GCN_or_GAT == "GCN":
        model = GNN(hidden_channels=64, out_channels=class_number)
    elif GCN_or_GAT =="GAT":
        model = GAT(hidden_channels=64, out_channels=class_number)

    model = to_hetero(model, data.metadata(), aggr='sum')
    model.to(device) # GPU

    optimizer = torch.optim.Adam(model.parameters(), lr=0.01, weight_decay=5e-4)

    #contagem de tempo
    start = time.time()

    # Training
    real_y_values = list(real_y_dict.values())
    L_loss = []
    for epoch in range(1, 1000):
        loss = train(model,optimizer)
        L_loss.append(loss)
        train_acc, test_acc = test(model,real_y_values,coarsened_to_not_coarsened)
        print(f'Epoch: {epoch:03d}, Loss: {loss:.4f}, Train: {train_acc:.4f}, Test: {test_acc:.4f}')
        df_temp = pd.DataFrame(L_loss)
        if len(df_temp >=5):
          loss_es =  pd.DataFrame(L_loss).tail(5)[0].std()
          print('Early stopping: ',loss_es)
          if loss_es <= 0.01:
            break

    #contagem de tempo
    end = time.time()

    # Creating Classification Report
    y_pred,y_true = get_y(model,real_y_values,coarsened_to_not_coarsened)
    y_pred = y_pred.cpu()
    y_true = y_true.cpu()

    class_dit = classification_report(y_true, y_pred, target_names=target_names, output_dict = True)

    print('\nClassification Report:\n')
    print(classification_report(y_true, y_pred, target_names=target_names))

    # Updating Dataframes
    df_list[i][0].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = class_dit['accuracy']               # acuracia
    df_list[i][1].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = class_dit['macro avg']['precision'] # precision
    df_list[i][2].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = class_dit['macro avg']['recall']    # recall
    df_list[i][3].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = class_dit['macro avg']['f1-score']  # f1-score
    df_list[i][4].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = class_dit['macro avg']['support']   # support
    df_list[i][5].at[model_name+"_"+GCN_or_GAT, str(rotulated)] = (end - start)                       # time

time: 17.6 ms (started: 2024-09-09 23:27:41 +00:00)


# Reorganizing files

In [ ]:
for keyphrase in ["keyphrase2","keyphrase3","keyphrase23"]:
    for rotulated in [1,5,10,20]:
        for iteration in range(10):
            os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source",
                      "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source")

            #count_ED("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf", dataset_name+"_"+keyphrase)
            os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf")
            #os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+"-timing.json")

            os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol",
                      "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol")

time: 6.83 s (started: 2024-09-09 23:29:09 +00:00)


In [ ]:
# for keyphrase in ["keyphrase2","keyphrase3","keyphrase23"]:
#     for rotulated in [1,5,10,20,30]:
#         for iteration in range(10):
#             os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source",
#                       "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source")

#             #count_ED("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf", dataset_name+"_"+keyphrase)
#             os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf")
#             #os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+"-timing.json")

#             os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol",
#                       "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol")

In [ ]:
# # Saving coarsening data dataframes
# for i in range(10):
#     df_list[i][6].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_coarse.pkl") # coarsening node and edges

In [ ]:
# Exlclui 80
# for keyphrase in ["keyphrase2","keyphrase3","keyphrase23"]:
#     for rotulated in [80]:
#         for iteration in range(10):
#             os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source")
#             # os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source",
#             #           "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".source")

#             os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf")
#             # os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".conf",
#             #           "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+str(rotulated)+'_'+str(iteration)+".conf")

#             os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol")
#             # os.rename("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol",
#             #          "/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated)+"/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+".ncol")

#             os.remove("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+"/drop_and_move/"+dataset_name+"_"+keyphrase+"_"+str(rotulated)+'_'+str(iteration)+"-timing.json")

--------------------------------------
# Hetrogenous Graph for Keyphrase = 2
--------------------------------------

In [ ]:
# Change here to change wich keypharse to use
keyphrase = "keyphrase2"

model_name = dataset_name+"_"+keyphrase

time: 508 µs (started: 2024-09-09 23:29:16 +00:00)


## Training

### rotulated base = 1 ❎

In [ ]:
rotulated=1

time: 325 µs (started: 2024-09-09 23:29:16 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 4797] },
  (concept, rev_has, document)={ edge_index=[2, 4797] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.9590, Train: 0.7500, Test: 0.4169
Early stopping:  nan
Epoch: 002, Loss: 17.1487, Train: 0.5000, Test: 0.1220
Early stopping:  10.0336749922301
Epoch: 003, Loss: 17.7918, Train: 0.5000, Test: 0.1864
Early stopping:  8.384263861940852
Epoch: 004, Loss: 9.9008, Train: 0.7500, Test: 0.4373
Early stopping:  6.980711482131895
Epoch: 005, Loss: 3.5528, Train: 0.7500, Test: 0.4000
Early stopping:  7.11692297154051
Epoch: 006, Loss: 2.1043, Train: 0.7500, Test: 0.3831
Early stopping:  7.343113342017045
Epoch: 007, Loss: 0.3001, Train: 1.0000, Test: 0.3729
Early stopping:  7.1633312209786135
Epoch: 008, Loss: 0.0007, Train: 1.0000, Test: 0.3288
Early stopping:  4.027015400405299
Epoc

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 5466] },
  (concept, rev_has, document)={ edge_index=[2, 5466] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 7.4837, Train: 0.2500, Test: 0.3356
Early stopping:  nan
Epoch: 002, Loss: 35.2178, Train: 0.2500, Test: 0.1661
Early stopping:  19.610981211385933
Epoch: 003, Loss: 26.7612, Train: 0.2500, Test: 0.4542
Early stopping:  14.214525980838374
Epoch: 004, Loss: 18.5456, Train: 0.5000, Test: 0.5051
Early stopping:  11.832650746708413
Epoch: 005, Loss: 8.7676, Train: 0.7500, Test: 0.5322
Early stopping:  11.833820699623871
Epoch: 006, Loss: 4.0925, Train: 0.7500, Test: 0.6203
Early stopping:  12.74632914936514
Epoch: 007, Loss: 1.3685, Train: 0.7500, Test: 0.4983
Early stopping:  10.567638710580683
Epoch: 008, Loss: 0.1971, Train: 1.0000, Test: 0.4983
Early stopping:  7.4506580642206

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 64.3 ms (started: 2024-09-09 23:29:51 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # time

time: 479 ms (started: 2024-09-09 23:29:51 +00:00)


### rotulated base = 5 ❎

In [ ]:
rotulated=5

time: 265 µs (started: 2024-09-09 23:29:51 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 4973] },
  (concept, rev_has, document)={ edge_index=[2, 4973] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.6564, Train: 0.5000, Test: 0.5341
Early stopping:  nan
Epoch: 002, Loss: 17.7640, Train: 0.2500, Test: 0.0717
Early stopping:  10.682749103352421
Epoch: 003, Loss: 21.9105, Train: 0.7000, Test: 0.4552
Early stopping:  10.133741977206764
Epoch: 004, Loss: 7.0257, Train: 0.7000, Test: 0.4946
Early stopping:  9.000533043577029
Epoch: 005, Loss: 4.3062, Train: 0.7500, Test: 0.5090
Early stopping:  8.582707138054898
Epoch: 006, Loss: 2.4058, Train: 0.7500, Test: 0.6129
Early stopping:  8.642163720675985
Epoch: 007, Loss: 0.7645, Train: 0.9000, Test: 0.6452
Early stopping:  8.502479935090976
Epoch: 008, Loss: 0.1440, Train: 0.9500, Test: 0.6416
Early stopping:  2.801551525683843
E

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 5356] },
  (concept, rev_has, document)={ edge_index=[2, 5356] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 4.9430, Train: 0.4500, Test: 0.2366
Early stopping:  nan
Epoch: 002, Loss: 19.2129, Train: 0.5000, Test: 0.3871
Early stopping:  10.090358794554584
Epoch: 003, Loss: 23.7761, Train: 0.4500, Test: 0.1900
Early stopping:  9.824637739120558
Epoch: 004, Loss: 16.7557, Train: 0.7000, Test: 0.4014
Early stopping:  8.031218687292862
Epoch: 005, Loss: 6.7482, Train: 0.7500, Test: 0.4839
Early stopping:  8.132449199415934
Epoch: 006, Loss: 1.9471, Train: 0.9500, Test: 0.7455
Early stopping:  9.051468234175843
Epoch: 007, Loss: 0.0943, Train: 0.8000, Test: 0.5842
Early stopping:  10.110336416438356
Epoch: 008, Loss: 1.1791, Train: 0.7000, Test: 0.5520
Early stopping:  6.867385012159063


In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 61.3 ms (started: 2024-09-09 23:30:23 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 447 ms (started: 2024-09-09 23:30:23 +00:00)


### rotulated base = 10 ❎

In [ ]:
rotulated=10

time: 1.67 ms (started: 2024-09-09 23:30:23 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 5420] },
  (concept, rev_has, document)={ edge_index=[2, 5420] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.6446, Train: 0.4000, Test: 0.5328
Early stopping:  nan
Epoch: 002, Loss: 18.3065, Train: 0.4000, Test: 0.3668
Early stopping:  10.36756182037122
Epoch: 003, Loss: 18.2062, Train: 0.5250, Test: 0.1583
Early stopping:  8.436273771322718
Epoch: 004, Loss: 11.3855, Train: 0.4750, Test: 0.1544
Early stopping:  6.960415962226886
Epoch: 005, Loss: 7.6601, Train: 0.7500, Test: 0.3591
Early stopping:  6.465053345075638
Epoch: 006, Loss: 1.9112, Train: 0.4750, Test: 0.3668
Early stopping:  7.035700017282197
Epoch: 007, Loss: 3.1798, Train: 0.6250, Test: 0.5830
Early stopping:  6.613509753764064
Epoch: 008, Loss: 2.1942, Train: 0.8250, Test: 0.6448
Early stopping:  4.129856429376559
Ep

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 6077] },
  (concept, rev_has, document)={ edge_index=[2, 6077] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 3.6469, Train: 0.2500, Test: 0.0618
Early stopping:  nan
Epoch: 002, Loss: 49.8000, Train: 0.2750, Test: 0.1544
Early stopping:  32.635158022786506
Epoch: 003, Loss: 34.6592, Train: 0.4250, Test: 0.4286
Early stopping:  23.526983373317297
Epoch: 004, Loss: 24.5473, Train: 0.5000, Test: 0.4402
Early stopping:  19.360373590496547
Epoch: 005, Loss: 12.2584, Train: 0.7500, Test: 0.4865
Early stopping:  18.21295806498557
Epoch: 006, Loss: 4.7706, Train: 0.7000, Test: 0.2548
Early stopping:  17.887906500139863
Epoch: 007, Loss: 2.8527, Train: 0.6000, Test: 0.2394
Early stopping:  13.546302753454139
Epoch: 008, Loss: 3.1266, Train: 0.6250, Test: 0.5598
Early stopping:  9.235861023243

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 47 ms (started: 2024-09-09 23:30:55 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 426 ms (started: 2024-09-09 23:30:55 +00:00)


### rotulated base = 20 ❎

In [ ]:
rotulated=20

time: 495 µs (started: 2024-09-09 23:30:56 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 6024] },
  (concept, rev_has, document)={ edge_index=[2, 6024] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.3415, Train: 0.3250, Test: 0.4932
Early stopping:  nan
Epoch: 002, Loss: 42.4418, Train: 0.3250, Test: 0.0274
Early stopping:  27.648045013052247
Epoch: 003, Loss: 44.1158, Train: 0.4750, Test: 0.1370
Early stopping:  23.072966439444855
Epoch: 004, Loss: 30.5299, Train: 0.4000, Test: 0.1279
Early stopping:  18.84110547645806
Epoch: 005, Loss: 19.8112, Train: 0.5625, Test: 0.1735
Early stopping:  16.95412001062832
Epoch: 006, Loss: 7.6749, Train: 0.7375, Test: 0.4795
Early stopping:  15.41644582355928
Epoch: 007, Loss: 2.1640, Train: 0.7500, Test: 0.4749
Early stopping:  17.02077544834207
Epoch: 008, Loss: 1.8058, Train: 0.6500, Test: 0.4566
Early stopping:  12.47957752548578

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/21 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[657, 384] },
  (document, has, concept)={ edge_index=[2, 5353] },
  (concept, rev_has, document)={ edge_index=[2, 5353] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 2.7870, Train: 0.6125, Test: 0.5708
Early stopping:  nan
Epoch: 002, Loss: 19.8786, Train: 0.2500, Test: 0.1187
Early stopping:  12.085543735764762
Epoch: 003, Loss: 35.5522, Train: 0.5000, Test: 0.1370
Early stopping:  16.387688884761566
Epoch: 004, Loss: 13.6811, Train: 0.3625, Test: 0.1644
Early stopping:  13.68324304831095
Epoch: 005, Loss: 11.5848, Train: 0.5750, Test: 0.5068
Early stopping:  12.189727648603549
Epoch: 006, Loss: 6.7635, Train: 0.6625, Test: 0.5753
Early stopping:  11.139844035256832
Epoch: 007, Loss: 4.0049, Train: 0.7750, Test: 0.6073
Early stopping:  12.471931486765662
Epoch: 008, Loss: 2.2239, Train: 0.8125, Test: 0.6164
Early stopping:  4.882915295373

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 60.5 ms (started: 2024-09-09 23:31:29 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 415 ms (started: 2024-09-09 23:31:29 +00:00)


### rotulated base = 30 ❎

In [ ]:
rotulated=30

time: 395 µs (started: 2024-09-08 12:58:13 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/126 [00:00<?, ?it/s]

Batches:   0%|          | 0/313 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4002, 384],
    y=[4002],
  },
  concept={ x=[10008, 384] },
  (document, has, concept)={ edge_index=[2, 52827] },
  (concept, rev_has, document)={ edge_index=[2, 52827] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 5.2398, Train: 0.1958, Test: 0.5421
Early stopping:  nan
Epoch: 002, Loss: 30.5828, Train: 0.2458, Test: 0.3219
Early stopping:  17.92016361420724
Epoch: 003, Loss: 33.2550, Train: 0.2875, Test: 0.0616
Early stopping:  15.461013771293507
Epoch: 004, Loss: 24.5772, Train: 0.5167, Test: 0.5826
Early stopping:  12.647672901337353
Epoch: 005, Loss: 19.6073, Train: 0.5917, Test: 0.6137
Early stopping:  11.084692140154178
Epoch: 006, Loss: 20.9110, Train: 0.7000, Test: 0.6695
Early stopping:  5.962328966345075
Epoch: 007, Loss: 16.1697, Train: 0.7333, Test: 0.5087
Early stopping:  6.5217838191310085
Epoch: 008, Loss: 8.1276, Train: 0.6458, Test: 0.3729
Early stopping:  6.22612

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/126 [00:00<?, ?it/s]

Batches:   0%|          | 0/313 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4005, 384],
    y=[4005],
  },
  concept={ x=[10008, 384] },
  (document, has, concept)={ edge_index=[2, 55124] },
  (concept, rev_has, document)={ edge_index=[2, 55124] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 7.4994, Train: 0.4583, Test: 0.5833
Early stopping:  nan
Epoch: 002, Loss: 10.3820, Train: 0.4042, Test: 0.2472
Early stopping:  2.0382489051446706
Epoch: 003, Loss: 60.8762, Train: 0.2875, Test: 0.3438
Early stopping:  30.019568230921383
Epoch: 004, Loss: 83.2771, Train: 0.3208, Test: 0.0995
Early stopping:  37.599647697731854
Epoch: 005, Loss: 41.0208, Train: 0.5000, Test: 0.6251
Early stopping:  32.56305568610813
Epoch: 006, Loss: 19.3192, Train: 0.4708, Test: 0.5901
Early stopping:  29.876545133307914
Epoch: 007, Loss: 29.1469, Train: 0.5000, Test: 0.5865
Early stopping:  25.63647435020369
Epoch: 008, Loss: 30.2913, Train: 0.6083, Test: 0.6503
Early stopping:  25.059

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 58.6 ms (started: 2024-09-08 13:01:53 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 406 ms (started: 2024-09-08 13:01:54 +00:00)


--------------------------------------
# Hetrogenous Graph for Keyphrase = 3
--------------------------------------

In [ ]:
# Change here to change wich keypharse to use
keyphrase = "keyphrase3"

model_name = dataset_name+"_"+keyphrase

time: 516 µs (started: 2024-09-09 23:31:29 +00:00)


## Training

### rotulated base = 1 ❎

In [ ]:
rotulated=1

time: 313 µs (started: 2024-09-09 23:31:29 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 6293] },
  (concept, rev_has, document)={ edge_index=[2, 6293] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.3277, Train: 0.7500, Test: 0.3017
Early stopping:  nan
Epoch: 002, Loss: 11.3097, Train: 0.2500, Test: 0.0847
Early stopping:  5.6441350049613686
Epoch: 003, Loss: 19.1597, Train: 0.7500, Test: 0.4678
Early stopping:  7.916099482099524
Epoch: 004, Loss: 3.9433, Train: 0.7500, Test: 0.4610
Early stopping:  7.428363236594296
Epoch: 005, Loss: 4.2428, Train: 0.7500, Test: 0.1831
Early stopping:  6.839405046482401
Epoch: 006, Loss: 5.4833, Train: 0.5000, Test: 0.1661
Early stopping:  6.499485535728518
Epoch: 007, Loss: 3.6502, Train: 1.0000, Test: 0.3288
Early stopping:  6.6687159837683865
Epoch: 008, Loss: 0.0022, Train: 1.0000, Test: 0.3525
Early stopping:  2.0574775069748044


...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5926] },
  (concept, rev_has, document)={ edge_index=[2, 5926] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 1.5755, Train: 0.2500, Test: 0.0814
Early stopping:  nan
Epoch: 002, Loss: 19.3433, Train: 0.7500, Test: 0.4068
Early stopping:  12.563732606662693
Epoch: 003, Loss: 2.7845, Train: 0.7500, Test: 0.3695
Early stopping:  9.927648293711984
Epoch: 004, Loss: 1.3860, Train: 1.0000, Test: 0.5627
Early stopping:  8.735958213548738
Epoch: 005, Loss: 0.0000, Train: 1.0000, Test: 0.6136
Early stopping:  8.06883741525405
Epoch: 006, Loss: 0.0000, Train: 1.0000, Test: 0.5831
Early stopping:  8.265244224396817
Epoch: 007, Loss: 0.0000, Train: 1.0000, Test: 0.5864
Early stopping:  1.2445794819807734
Epoch: 008, Loss: 0.0000, Train: 1.0000, Test: 0.5661
Early stopping:  0.6198519844282514
Ep

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 7410] },
  (concept, rev_has, document)={ edge_index=[2, 7410] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 6.5409, Train: 0.2500, Test: 0.3356
Early stopping:  nan
Epoch: 002, Loss: 40.9623, Train: 0.2500, Test: 0.1525
Early stopping:  24.339562923543458
Epoch: 003, Loss: 53.1354, Train: 0.2500, Test: 0.0814
Early stopping:  24.166296347831004
Epoch: 004, Loss: 57.0634, Train: 0.2500, Test: 0.1220
Early stopping:  22.969635968919643
Epoch: 005, Loss: 19.1497, Train: 0.7500, Test: 0.4678
Early stopping:  21.861487887098654
Epoch: 006, Loss: 7.8608, Train: 0.2500, Test: 0.3797
Early stopping:  21.430048849163295
Epoch: 007, Loss: 8.9340, Train: 0.2500, Test: 0.3831
Early stopping:  24.0642255944544
Epoch: 008, Loss: 7.8486, Train: 0.7500, Test: 0.4814
Early stopping:  21.164484149434

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 61.4 ms (started: 2024-09-09 23:31:48 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 391 ms (started: 2024-09-09 23:31:48 +00:00)


### rotulated base = 5 ❎

In [ ]:
rotulated=5

time: 545 µs (started: 2024-09-09 23:31:49 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5177] },
  (concept, rev_has, document)={ edge_index=[2, 5177] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.2829, Train: 0.7500, Test: 0.5233
Early stopping:  nan
Epoch: 002, Loss: 11.4220, Train: 0.7500, Test: 0.5448
Early stopping:  6.462312893315222
Epoch: 003, Loss: 4.7376, Train: 0.9500, Test: 0.6559
Early stopping:  4.729850297435186
Epoch: 004, Loss: 0.3376, Train: 0.7000, Test: 0.4050
Early stopping:  4.832494651288864
Epoch: 005, Loss: 1.4904, Train: 0.9000, Test: 0.4373
Early stopping:  4.423654783126936
Epoch: 006, Loss: 0.6563, Train: 0.9500, Test: 0.5376
Early stopping:  4.640939105152826
Epoch: 007, Loss: 0.0582, Train: 1.0000, Test: 0.5699
Early stopping:  1.9114506792405934
Epoch: 008, Loss: 0.0385, Train: 0.9500, Test: 0.5699
Early stopping:  0.599696376457899
Epo

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 6128] },
  (concept, rev_has, document)={ edge_index=[2, 6128] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 5.4040, Train: 0.5000, Test: 0.4480
Early stopping:  nan
Epoch: 002, Loss: 44.8049, Train: 0.2500, Test: 0.3405
Early stopping:  27.860657993525937
Epoch: 003, Loss: 39.1115, Train: 0.3500, Test: 0.4767
Early stopping:  21.29571402383615
Epoch: 004, Loss: 29.9141, Train: 0.4500, Test: 0.4731
Early stopping:  17.388019939030503
Epoch: 005, Loss: 16.8311, Train: 0.5500, Test: 0.5412
Early stopping:  16.1381713423675
Epoch: 006, Loss: 4.4740, Train: 0.8000, Test: 0.7670
Early stopping:  16.45463312188351
Epoch: 007, Loss: 2.0580, Train: 0.7000, Test: 0.5018
Early stopping:  16.007571586977217
Epoch: 008, Loss: 2.6413, Train: 0.7000, Test: 0.4946
Early stopping:  12.08298359287461

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5315] },
  (concept, rev_has, document)={ edge_index=[2, 5315] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 4.8277, Train: 0.2500, Test: 0.1470
Early stopping:  nan
Epoch: 002, Loss: 26.0275, Train: 0.5000, Test: 0.4552
Early stopping:  14.990493690191697
Epoch: 003, Loss: 21.0476, Train: 0.4500, Test: 0.4588
Early stopping:  11.085380635652374
Epoch: 004, Loss: 11.7216, Train: 0.8500, Test: 0.5269
Early stopping:  9.471325049241525
Epoch: 005, Loss: 1.4946, Train: 0.9500, Test: 0.5842
Early stopping:  10.431576864649042
Epoch: 006, Loss: 0.7360, Train: 0.7500, Test: 0.4731
Early stopping:  11.354913259128887
Epoch: 007, Loss: 2.5524, Train: 0.7000, Test: 0.4624
Early stopping:  8.770040378494016
Epoch: 008, Loss: 2.9236, Train: 0.8500, Test: 0.5018
Early stopping:  4.46493726918019

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 48.5 ms (started: 2024-09-09 23:32:09 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 446 ms (started: 2024-09-09 23:32:09 +00:00)


### rotulated base = 10 ❎

In [ ]:
rotulated=10

time: 541 µs (started: 2024-09-09 23:32:09 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5602] },
  (concept, rev_has, document)={ edge_index=[2, 5602] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.7980, Train: 0.4250, Test: 0.1351
Early stopping:  nan
Epoch: 002, Loss: 22.8082, Train: 0.5000, Test: 0.2317
Early stopping:  13.442219094900361
Epoch: 003, Loss: 25.5531, Train: 0.5000, Test: 0.4402
Early stopping:  11.847694272904725
Epoch: 004, Loss: 16.7109, Train: 0.6250, Test: 0.2355
Early stopping:  9.679496208769057
Epoch: 005, Loss: 5.9731, Train: 0.7000, Test: 0.2355
Early stopping:  9.775319778674795
Epoch: 006, Loss: 1.6904, Train: 0.6750, Test: 0.3127
Early stopping:  10.402724016103772
Epoch: 007, Loss: 1.2489, Train: 0.7250, Test: 0.3552
Early stopping:  10.588983727869465
Epoch: 008, Loss: 1.3918, Train: 0.8000, Test: 0.5637
Early stopping:  6.62049447570393

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5358] },
  (concept, rev_has, document)={ edge_index=[2, 5358] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 2.9143, Train: 0.2500, Test: 0.4556
Early stopping:  nan
Epoch: 002, Loss: 18.9605, Train: 0.8750, Test: 0.4942
Early stopping:  11.346340780738018
Epoch: 003, Loss: 0.5322, Train: 0.7250, Test: 0.4440
Early stopping:  10.022943585465512
Epoch: 004, Loss: 5.3238, Train: 0.7000, Test: 0.4324
Early stopping:  8.25368947436271
Epoch: 005, Loss: 4.8375, Train: 0.8000, Test: 0.4672
Early stopping:  7.209059319329724
Epoch: 006, Loss: 1.8376, Train: 0.9500, Test: 0.5135
Early stopping:  7.357995365232162
Epoch: 007, Loss: 0.5916, Train: 0.9500, Test: 0.7375
Early stopping:  2.3083053942319998
Epoch: 008, Loss: 0.1479, Train: 0.9750, Test: 0.7452
Early stopping:  2.399959004751609
Ep

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5375] },
  (concept, rev_has, document)={ edge_index=[2, 5375] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 2.2985, Train: 0.3750, Test: 0.5058
Early stopping:  nan
Epoch: 002, Loss: 32.4167, Train: 0.2500, Test: 0.3475
Early stopping:  21.29680457560348
Epoch: 003, Loss: 34.7387, Train: 0.2500, Test: 0.3475
Early stopping:  18.096346520553016
Epoch: 004, Loss: 13.3252, Train: 0.8250, Test: 0.5985
Early stopping:  15.571012274745998
Epoch: 005, Loss: 1.4214, Train: 0.6500, Test: 0.5560
Early stopping:  16.004213483866707
Epoch: 006, Loss: 5.0182, Train: 0.6750, Test: 0.5521
Early stopping:  15.422046257315982
Epoch: 007, Loss: 5.5105, Train: 0.6500, Test: 0.5290
Early stopping:  13.43102187242185
Epoch: 008, Loss: 3.8176, Train: 0.6500, Test: 0.3282
Early stopping:  4.48397561257370

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 53.7 ms (started: 2024-09-09 23:32:29 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 448 ms (started: 2024-09-09 23:32:29 +00:00)


### rotulated base = 20 ❎

In [ ]:
rotulated=20

time: 460 µs (started: 2024-09-09 23:32:30 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 4898] },
  (concept, rev_has, document)={ edge_index=[2, 4898] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.9821, Train: 0.5500, Test: 0.1644
Early stopping:  nan
Epoch: 002, Loss: 13.4933, Train: 0.5000, Test: 0.3744
Early stopping:  6.7254417377149185
Epoch: 003, Loss: 15.8550, Train: 0.5875, Test: 0.4110
Early stopping:  6.2849855409026745
Epoch: 004, Loss: 8.9090, Train: 0.8250, Test: 0.4658
Early stopping:  5.248362036784493
Epoch: 005, Loss: 2.2713, Train: 0.9125, Test: 0.3105
Early stopping:  5.8650593156461355
Epoch: 006, Loss: 0.9250, Train: 0.8125, Test: 0.5982
Early stopping:  6.617306506135225
Epoch: 007, Loss: 1.3548, Train: 0.7625, Test: 0.5845
Early stopping:  6.456120006016407
Epoch: 008, Loss: 2.6289, Train: 0.8125, Test: 0.5936
Early stopping:  3.2542224072721386

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5218] },
  (concept, rev_has, document)={ edge_index=[2, 5218] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 2.5362, Train: 0.3250, Test: 0.5068
Early stopping:  nan
Epoch: 002, Loss: 19.1205, Train: 0.4625, Test: 0.3744
Early stopping:  11.72687506646142
Epoch: 003, Loss: 17.4714, Train: 0.5000, Test: 0.3470
Early stopping:  9.136194344680531
Epoch: 004, Loss: 11.2385, Train: 0.6125, Test: 0.3836
Early stopping:  7.51401846272119
Epoch: 005, Loss: 4.7750, Train: 0.8125, Test: 0.5616
Early stopping:  7.386843131570889
Epoch: 006, Loss: 1.3435, Train: 0.9000, Test: 0.6164
Early stopping:  7.740408142812996
Epoch: 007, Loss: 0.7810, Train: 0.8625, Test: 0.6073
Early stopping:  7.126778877312752
Epoch: 008, Loss: 1.1207, Train: 0.7500, Test: 0.5845
Early stopping:  4.432711938699115
Epo

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/23 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[711, 384] },
  (document, has, concept)={ edge_index=[2, 5731] },
  (concept, rev_has, document)={ edge_index=[2, 5731] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 1.0586, Train: 0.2500, Test: 0.1187
Early stopping:  nan
Epoch: 002, Loss: 50.2352, Train: 0.5500, Test: 0.1598
Early stopping:  34.773134716583954
Epoch: 003, Loss: 5.2521, Train: 0.7000, Test: 0.6073
Early stopping:  27.262332359433017
Epoch: 004, Loss: 2.8059, Train: 0.7625, Test: 0.7306
Early stopping:  23.660774494590868
Epoch: 005, Loss: 2.1691, Train: 0.8250, Test: 0.7352
Early stopping:  21.259691143760392
Epoch: 006, Loss: 1.3718, Train: 0.9125, Test: 0.7900
Early stopping:  21.218696268256995
Epoch: 007, Loss: 0.6637, Train: 0.7250, Test: 0.7260
Early stopping:  1.761451278282139
Epoch: 008, Loss: 1.3088, Train: 0.8625, Test: 0.6347
Early stopping:  0.832349873348306

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 66.3 ms (started: 2024-09-09 23:32:52 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 429 ms (started: 2024-09-09 23:32:52 +00:00)


### rotulated base = 30 ❎

In [ ]:
rotulated=30

time: 384 µs (started: 2024-09-08 13:14:39 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/148 [00:00<?, ?it/s]

Batches:   0%|          | 0/403 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4734, 384],
    y=[4734],
  },
  concept={ x=[12878, 384] },
  (document, has, concept)={ edge_index=[2, 60418] },
  (concept, rev_has, document)={ edge_index=[2, 60418] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.1170, Train: 0.4667, Test: 0.1067
Early stopping:  nan
Epoch: 002, Loss: 39.8589, Train: 0.5417, Test: 0.1153
Early stopping:  25.980424535531764
Epoch: 003, Loss: 13.7277, Train: 0.8083, Test: 0.7830
Early stopping:  18.909391891481867
Epoch: 004, Loss: 1.7487, Train: 0.7083, Test: 0.5880
Early stopping:  17.66150603463064
Epoch: 005, Loss: 2.3278, Train: 0.7208, Test: 0.7943
Early stopping:  16.252141942143876
Epoch: 006, Loss: 3.8373, Train: 0.7417, Test: 0.7984
Early stopping:  16.15488846205164
Epoch: 007, Loss: 3.8738, Train: 0.8333, Test: 0.7316
Early stopping:  4.9104781007783975
Epoch: 008, Loss: 2.7890, Train: 0.7500, Test: 0.4524
Early stopping:  0.934197631

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/150 [00:00<?, ?it/s]

Batches:   0%|          | 0/403 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4772, 384],
    y=[4772],
  },
  concept={ x=[12878, 384] },
  (document, has, concept)={ edge_index=[2, 61613] },
  (concept, rev_has, document)={ edge_index=[2, 61613] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 5.9468, Train: 0.4500, Test: 0.5877
Early stopping:  nan
Epoch: 002, Loss: 10.3284, Train: 0.5708, Test: 0.4069
Early stopping:  3.0982829433430137
Epoch: 003, Loss: 20.0611, Train: 0.7458, Test: 0.8150
Early stopping:  7.224225407210924
Epoch: 004, Loss: 5.7619, Train: 0.7792, Test: 0.7717
Early stopping:  6.698825732367153
Epoch: 005, Loss: 7.6020, Train: 0.7333, Test: 0.3792
Early stopping:  5.946756689616436
Epoch: 006, Loss: 7.9912, Train: 0.7667, Test: 0.7941
Early stopping:  5.667266825586572
Epoch: 007, Loss: 4.6957, Train: 0.7042, Test: 0.6628
Early stopping:  6.206534828975676
Epoch: 008, Loss: 3.6300, Train: 0.7333, Test: 0.6704
Early stopping:  1.863183466574

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 46.2 ms (started: 2024-09-08 13:18:27 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 470 ms (started: 2024-09-08 13:18:27 +00:00)


--------------------------------------
# Hetrogenous Graph for Keyphrase = 23
--------------------------------------

In [ ]:
# Change here to change wich keypharse to use
keyphrase = "keyphrase23"

model_name = dataset_name+"_"+keyphrase

time: 584 µs (started: 2024-09-09 23:32:53 +00:00)


## Training

### rotulated base = 1 ❎

In [ ]:
rotulated=1

time: 250 µs (started: 2024-09-09 23:32:53 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5468] },
  (concept, rev_has, document)={ edge_index=[2, 5468] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.5776, Train: 0.2500, Test: 0.3390
Early stopping:  nan
Epoch: 002, Loss: 17.4108, Train: 0.5000, Test: 0.0847
Early stopping:  10.488687479719285
Epoch: 003, Loss: 15.7584, Train: 0.5000, Test: 0.4644
Early stopping:  8.129067906122913
Epoch: 004, Loss: 12.9088, Train: 0.5000, Test: 0.4610
Early stopping:  6.6559085372020315
Epoch: 005, Loss: 4.3636, Train: 0.7500, Test: 0.3695
Early stopping:  6.737572120715065
Epoch: 006, Loss: 1.3846, Train: 0.5000, Test: 0.3695
Early stopping:  7.104024906758374
Epoch: 007, Loss: 1.7926, Train: 0.7500, Test: 0.3932
Early stopping:  6.6507993758298545
Epoch: 008, Loss: 0.9708, Train: 1.0000, Test: 0.4136
Early stopping:  4.999611314673998

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5145] },
  (concept, rev_has, document)={ edge_index=[2, 5145] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 1.5625, Train: 0.7500, Test: 0.1220
Early stopping:  nan
Epoch: 002, Loss: 8.6346, Train: 0.5000, Test: 0.5051
Early stopping:  5.00073394394231
Epoch: 003, Loss: 3.8483, Train: 1.0000, Test: 0.4102
Early stopping:  3.608977000486758
Epoch: 004, Loss: 0.0000, Train: 1.0000, Test: 0.5119
Early stopping:  3.763362087883515
Epoch: 005, Loss: 0.0000, Train: 1.0000, Test: 0.4780
Early stopping:  3.617737278018072
Epoch: 006, Loss: 0.0801, Train: 1.0000, Test: 0.4644
Early stopping:  3.8015103813155746
Epoch: 007, Loss: 0.0623, Train: 1.0000, Test: 0.4610
Early stopping:  1.7054623412926284
Epoch: 008, Loss: 0.0011, Train: 1.0000, Test: 0.4644
Early stopping:  0.039301185766664665
E

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5170] },
  (concept, rev_has, document)={ edge_index=[2, 5170] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 3.8444, Train: 0.5000, Test: 0.4814
Early stopping:  nan
Epoch: 002, Loss: 14.6963, Train: 0.5000, Test: 0.3085
Early stopping:  7.673396178954788
Epoch: 003, Loss: 18.9203, Train: 0.2500, Test: 0.4271
Early stopping:  7.776935837092651
Epoch: 004, Loss: 12.1787, Train: 0.5000, Test: 0.4542
Early stopping:  6.351712703883707
Epoch: 005, Loss: 2.9939, Train: 1.0000, Test: 0.5932
Early stopping:  6.92750951050609
Epoch: 006, Loss: 0.1670, Train: 1.0000, Test: 0.7322
Early stopping:  7.936115402276591
Epoch: 007, Loss: 0.0013, Train: 1.0000, Test: 0.6576
Early stopping:  8.374398414209551
Epoch: 008, Loss: 0.0003, Train: 1.0000, Test: 0.6136
Early stopping:  5.249778146030075
Epo

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 45.7 ms (started: 2024-09-09 23:33:10 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 456 ms (started: 2024-09-09 23:33:10 +00:00)


### rotulated base = 5 ❎

In [ ]:
rotulated=5

time: 364 µs (started: 2024-09-09 23:33:11 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5540] },
  (concept, rev_has, document)={ edge_index=[2, 5540] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.7179, Train: 0.2500, Test: 0.0860
Early stopping:  nan
Epoch: 002, Loss: 22.5700, Train: 0.2500, Test: 0.3405
Early stopping:  14.037538103907524
Epoch: 003, Loss: 25.6287, Train: 0.4500, Test: 0.6487
Early stopping:  12.438949013135993
Epoch: 004, Loss: 15.4986, Train: 0.6000, Test: 0.6380
Early stopping:  10.183049463932422
Epoch: 005, Loss: 6.7425, Train: 0.8500, Test: 0.6487
Early stopping:  9.860005808394991
Epoch: 006, Loss: 2.5923, Train: 0.9000, Test: 0.6667
Early stopping:  9.898031754287754
Epoch: 007, Loss: 0.5826, Train: 0.9500, Test: 0.7491
Early stopping:  10.349454628048461
Epoch: 008, Loss: 0.0488, Train: 0.9500, Test: 0.5591
Early stopping:  6.38433654699734

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5113] },
  (concept, rev_has, document)={ edge_index=[2, 5113] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 2.1469, Train: 0.4500, Test: 0.1720
Early stopping:  nan
Epoch: 002, Loss: 28.5281, Train: 0.4500, Test: 0.3871
Early stopping:  18.654332549647844
Epoch: 003, Loss: 21.5918, Train: 0.5500, Test: 0.4588
Early stopping:  13.675928211123182
Epoch: 004, Loss: 9.6641, Train: 0.7000, Test: 0.4875
Early stopping:  11.820931108476243
Epoch: 005, Loss: 2.4660, Train: 0.8000, Test: 0.5556
Early stopping:  11.776586979737038
Epoch: 006, Loss: 1.4198, Train: 0.5500, Test: 0.5663
Early stopping:  11.945507161328747
Epoch: 007, Loss: 3.1364, Train: 0.7000, Test: 0.5735
Early stopping:  8.433451172939284
Epoch: 008, Loss: 2.2076, Train: 0.9000, Test: 0.5878
Early stopping:  3.34689709628177

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5365] },
  (concept, rev_has, document)={ edge_index=[2, 5365] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 3.9107, Train: 0.6000, Test: 0.2796
Early stopping:  nan
Epoch: 002, Loss: 22.7495, Train: 0.6500, Test: 0.5018
Early stopping:  13.321063258408763
Epoch: 003, Loss: 14.1803, Train: 0.5500, Test: 0.5054
Early stopping:  9.43219430856552
Epoch: 004, Loss: 8.3219, Train: 0.6000, Test: 0.3047
Early stopping:  8.143164378282812
Epoch: 005, Loss: 2.6068, Train: 0.8000, Test: 0.3513
Early stopping:  8.275780092467224
Epoch: 006, Loss: 1.1012, Train: 0.9000, Test: 0.5305
Early stopping:  8.894849841567167
Epoch: 007, Loss: 0.9366, Train: 0.8500, Test: 0.5233
Early stopping:  5.740871812646033
Epoch: 008, Loss: 0.9520, Train: 0.9000, Test: 0.5412
Early stopping:  3.174155401812274
Epo

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 62.1 ms (started: 2024-09-09 23:33:31 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 404 ms (started: 2024-09-09 23:33:31 +00:00)


### rotulated base = 10 ❎

In [ ]:
rotulated=10

time: 345 µs (started: 2024-09-09 23:33:31 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5165] },
  (concept, rev_has, document)={ edge_index=[2, 5165] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 2.5406, Train: 0.4750, Test: 0.3552
Early stopping:  nan
Epoch: 002, Loss: 26.5285, Train: 0.4750, Test: 0.1429
Early stopping:  16.96200440941852
Epoch: 003, Loss: 23.9252, Train: 0.2500, Test: 0.1429
Early stopping:  13.16243103586536
Epoch: 004, Loss: 15.9404, Train: 0.7250, Test: 0.2278
Early stopping:  10.781607210867833
Epoch: 005, Loss: 3.4559, Train: 0.9000, Test: 0.5637
Early stopping:  11.186940465273244
Epoch: 006, Loss: 0.5797, Train: 0.8250, Test: 0.5792
Early stopping:  11.731193941620102
Epoch: 007, Loss: 0.7013, Train: 0.7000, Test: 0.5521
Early stopping:  10.504841644353128
Epoch: 008, Loss: 2.0847, Train: 0.8250, Test: 0.5753
Early stopping:  6.47287475958734

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 6408] },
  (concept, rev_has, document)={ edge_index=[2, 6408] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 3.3706, Train: 0.3250, Test: 0.3784
Early stopping:  nan
Epoch: 002, Loss: 30.4106, Train: 0.2500, Test: 0.4556
Early stopping:  19.120119457490354
Epoch: 003, Loss: 35.1136, Train: 0.3250, Test: 0.0811
Early stopping:  17.131309171945084
Epoch: 004, Loss: 32.4282, Train: 0.3500, Test: 0.0888
Early stopping:  14.766281075338457
Epoch: 005, Loss: 19.2309, Train: 0.6500, Test: 0.1853
Early stopping:  13.075697065079646
Epoch: 006, Loss: 2.6277, Train: 0.9500, Test: 0.7799
Early stopping:  13.371195915145584
Epoch: 007, Loss: 0.3938, Train: 0.8250, Test: 0.5212
Early stopping:  16.1929146532177
Epoch: 008, Loss: 1.3989, Train: 0.7000, Test: 0.4942
Early stopping:  14.154969427990

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5306] },
  (concept, rev_has, document)={ edge_index=[2, 5306] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 2.3997, Train: 0.4750, Test: 0.4595
Early stopping:  nan
Epoch: 002, Loss: 31.9559, Train: 0.4750, Test: 0.2355
Early stopping:  20.899397389134624
Epoch: 003, Loss: 11.4764, Train: 0.8250, Test: 0.3938
Early stopping:  15.140266084209578
Epoch: 004, Loss: 1.4796, Train: 0.5750, Test: 0.5097
Early stopping:  14.15672263906638
Epoch: 005, Loss: 1.9783, Train: 0.5750, Test: 0.5097
Early stopping:  13.02737971435163
Epoch: 006, Loss: 1.9239, Train: 0.7500, Test: 0.6062
Early stopping:  13.097025157221074
Epoch: 007, Loss: 0.8595, Train: 0.8000, Test: 0.6525
Early stopping:  4.457221314504199
Epoch: 008, Loss: 0.5498, Train: 0.8750, Test: 0.6564
Early stopping:  0.6366811120550111

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 64 ms (started: 2024-09-09 23:33:51 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 422 ms (started: 2024-09-09 23:33:51 +00:00)


### rotulated base = 20 ❎

In [ ]:
rotulated=20

time: 424 µs (started: 2024-09-09 23:33:51 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

================ Creating Embeddings ================


/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 4861] },
  (concept, rev_has, document)={ edge_index=[2, 4861] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 1.6757, Train: 0.4875, Test: 0.5023
Early stopping:  nan
Epoch: 002, Loss: 16.3217, Train: 0.5500, Test: 0.0959
Early stopping:  10.356257782719506
Epoch: 003, Loss: 6.3219, Train: 0.7125, Test: 0.4429
Early stopping:  7.484280046403439
Epoch: 004, Loss: 5.6794, Train: 0.6750, Test: 0.4612
Early stopping:  6.230215979705533
Epoch: 005, Loss: 5.3035, Train: 0.7625, Test: 0.2329
Early stopping:  5.484184909138381
Epoch: 006, Loss: 3.9303, Train: 0.8375, Test: 0.2740
Early stopping:  5.00226862852294
Epoch: 007, Loss: 2.4918, Train: 0.9000, Test: 0.5753
Early stopping:  1.533964665892553
Epoch: 008, Loss: 1.6875, Train: 0.8875, Test: 0.5845
Early stopping:  1.7307594794629872
Epo

...

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5019] },
  (concept, rev_has, document)={ edge_index=[2, 5019] }
)
================ Training GCN ================

================ GCN - MODEL 8 ================

Epoch: 001, Loss: 3.2613, Train: 0.2500, Test: 0.1187
Early stopping:  nan
Epoch: 002, Loss: 30.4106, Train: 0.3375, Test: 0.5068
Early stopping:  19.19742453267946
Epoch: 003, Loss: 20.1531, Train: 0.3750, Test: 0.5114
Early stopping:  13.709060389790343
Epoch: 004, Loss: 9.8346, Train: 0.5500, Test: 0.4658
Early stopping:  11.904751386831663
Epoch: 005, Loss: 5.8240, Train: 0.7625, Test: 0.5388
Early stopping:  11.254225971353327
Epoch: 006, Loss: 2.4480, Train: 0.8625, Test: 0.5753
Early stopping:  11.450536809819077
Epoch: 007, Loss: 1.2224, Train: 0.8750, Test: 0.5890
Early stopping:  7.6240598296238895
Epoch: 008, Loss: 1.0306, Train: 0.8875, Test: 0.5845
Early stopping:  3.75117195139883

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


Batches:   0%|          | 0/5 [00:00<?, ?it/s]

Batches:   0%|          | 0/22 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[149, 384],
    y=[149],
  },
  concept={ x=[696, 384] },
  (document, has, concept)={ edge_index=[2, 5245] },
  (concept, rev_has, document)={ edge_index=[2, 5245] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 3.3579, Train: 0.4500, Test: 0.6667
Early stopping:  nan
Epoch: 002, Loss: 27.2899, Train: 0.3375, Test: 0.0548
Early stopping:  16.922515341174723
Epoch: 003, Loss: 22.7292, Train: 0.5375, Test: 0.4018
Early stopping:  12.706901733470643
Epoch: 004, Loss: 10.7791, Train: 0.7000, Test: 0.5753
Early stopping:  10.951706298626306
Epoch: 005, Loss: 2.9164, Train: 0.6375, Test: 0.5936
Early stopping:  11.15327355750426
Epoch: 006, Loss: 2.0560, Train: 0.8750, Test: 0.6301
Early stopping:  11.457775139502441
Epoch: 007, Loss: 0.6206, Train: 0.7500, Test: 0.5753
Early stopping:  9.221453352423978
Epoch: 008, Loss: 1.5505, Train: 0.7125, Test: 0.6758
Early stopping:  4.10690684103652

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 62.1 ms (started: 2024-09-09 23:34:14 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 402 ms (started: 2024-09-09 23:34:14 +00:00)


### rotulated base = 30 ❎

In [ ]:
rotulated=30

time: 402 µs (started: 2024-09-08 13:31:09 +00:00)


In [ ]:
for iteration in range(10):
    # Define embedding
    new_document_nodes_text, new_context_nodes_text = get_nodes(model_name,rotulated,iteration)

    print(f"================ Creating Embeddings ================")
    document_nodes_embeddings,context_nodes_embeddings = create_embeddings(rotulated,iteration,new_document_nodes_text,new_context_nodes_text)

    # Define grafo
    data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes = set_up_graph(model_name,rotulated,iteration,document_nodes_embeddings,context_nodes_embeddings)

    # Treina GCN
    print(f"================ Training GCN ================")
    training_iteration(iteration, rotulated, 'GCN', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

    # Treina GAT
    print(f"================ Training GAT ================")
    training_iteration(iteration, rotulated, 'GAT', data, real_y_dict, new_train_mask, new_val_mask, new_test_mask, coarsened_to_not_coarsened, class_number, classes)

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/143 [00:00<?, ?it/s]

Batches:   0%|          | 0/402 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4574, 384],
    y=[4574],
  },
  concept={ x=[12863, 384] },
  (document, has, concept)={ edge_index=[2, 57913] },
  (concept, rev_has, document)={ edge_index=[2, 57913] }
)
================ Training GCN ================

================ GCN - MODEL 0 ================

Epoch: 001, Loss: 3.8781, Train: 0.4375, Test: 0.5866
Early stopping:  nan
Epoch: 002, Loss: 5.7160, Train: 0.4917, Test: 0.3641
Early stopping:  1.2995736286612811
Epoch: 003, Loss: 13.7030, Train: 0.6375, Test: 0.6536
Early stopping:  5.223317649400673
Epoch: 004, Loss: 5.2553, Train: 0.6958, Test: 0.6190
Early stopping:  4.445690457225015
Epoch: 005, Loss: 8.6216, Train: 0.7333, Test: 0.6195
Early stopping:  3.906826080406485
Epoch: 006, Loss: 10.0149, Train: 0.7417, Test: 0.6229
Early stopping:  3.447027899649781
Epoch: 007, Loss: 9.0044, Train: 0.8083, Test: 0.7116
Early stopping:  3.0332460186703134
Epoch: 008, Loss: 6.4408, Train: 0.8833, Test: 0.7819
Early stopping:  1.95777250554

...

/usr/local/lib/python3.10/dist-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(io.BytesIO(b))


================ Creating Embeddings ================


Batches:   0%|          | 0/143 [00:00<?, ?it/s]

Batches:   0%|          | 0/402 [00:00<?, ?it/s]

HeteroData(
  document={
    x=[4554, 384],
    y=[4554],
  },
  concept={ x=[12863, 384] },
  (document, has, concept)={ edge_index=[2, 58840] },
  (concept, rev_has, document)={ edge_index=[2, 58840] }
)
================ Training GCN ================

================ GCN - MODEL 9 ================

Epoch: 001, Loss: 4.1676, Train: 0.3750, Test: 0.5738
Early stopping:  nan
Epoch: 002, Loss: 7.8675, Train: 0.6875, Test: 0.6734
Early stopping:  2.616233589708879
Epoch: 003, Loss: 3.1725, Train: 0.6417, Test: 0.5884
Early stopping:  2.473955540180057
Epoch: 004, Loss: 3.6014, Train: 0.6333, Test: 0.1868
Early stopping:  2.149170354331956
Epoch: 005, Loss: 4.8281, Train: 0.7500, Test: 0.7206
Early stopping:  1.8620866672825969
Epoch: 006, Loss: 4.9972, Train: 0.7417, Test: 0.7476
Early stopping:  1.8365190490960757
Epoch: 007, Loss: 5.7598, Train: 0.6750, Test: 0.4169
Early stopping:  1.0615603535710916
Epoch: 008, Loss: 7.3942, Train: 0.7542, Test: 0.7926
Early stopping:  1.396015277219

In [ ]:
# Try to delete the file.
try:
    shutil.rmtree("/content/drive/MyDrive/mestrado_v2/processed_datasets/"+dataset_name+'/'+keyphrase+"/graphs_rotulated_"+str(rotulated))
except OSError as e:
    # If it fails, inform the user.
    print("Error: %s - %s." % (e.filename, e.strerror))

time: 56.5 ms (started: 2024-09-08 13:34:58 +00:00)


#### Saving dataframes

In [ ]:
# Saving dataframes
for i in range(10):
    df_list[i][0].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_acc.pkl") # acuracia
    df_list[i][1].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_pre.pkl") # precision
    df_list[i][2].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_rec.pkl") # recall
    df_list[i][3].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_f1.pkl")  # f1-score
    df_list[i][4].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_sup.pkl") # support
    df_list[i][5].to_pickle("/content/drive/MyDrive/mestrado_v2/processed_datasets/dataframes/"+str(i)+"/df_time.pkl") # support

time: 472 ms (started: 2024-09-08 13:34:58 +00:00)


# Show dataframe

In [ ]:
df_list[0][5]

1          5         10         20  \
Industry_Sector_keyphrase2_GCN   5.967893  14.137134  19.774683   7.163521   
Industry_Sector_keyphrase2_GAT   2.891018   5.089645   4.946186   6.673805   
Industry_Sector_keyphrase3_GCN   5.692917  13.041445  21.713131  16.310932   
Industry_Sector_keyphrase3_GAT   2.746514   4.288752   5.765436   6.155356   
Industry_Sector_keyphrase23_GCN  4.684616  13.329979  20.220493  26.668284   
...                                   ...        ...        ...        ...   
CSTR_keyphrase2_GAT              0.435348   0.244198   0.273186   0.698544   
CSTR_keyphrase3_GCN              0.269534    0.18328   0.294987   0.397386   
CSTR_keyphrase3_GAT              0.321474   0.244007   0.262077    0.34874   
CSTR_keyphrase23_GCN             0.140508   0.391227   0.323581   0.442196   
CSTR_keyphrase23_GAT             0.217168   0.314018   0.281713   0.504065   

                                       30  
Industry_Sector_keyphrase2_GCN   4.032328  
Industry_Sector_keyphrase2_GAT   5.501309  
Industry_Sector_keyphrase3_GCN   6.837297  
Industry_Sector_keyphrase3_GAT   7.282659  
Industry_Sector_keyphrase23_GCN  39.06455  
...                                   ...  
CSTR_keyphrase2_GAT                   NaN  
CSTR_keyphrase3_GCN                   NaN  
CSTR_keyphrase3_GAT                   NaN  
CSTR_keyphrase23_GCN                  NaN  
CSTR_keyphrase23_GAT                  NaN  

[72 rows x 5 columns]

time: 21.9 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[0][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.151218  0.407645    0.4564  0.488202   
Dmoz_Computers_keyphrase2_GAT    0.229919  0.432088  0.472849  0.527555   
Dmoz_Computers_keyphrase3_GCN    0.207264  0.438612  0.500523   0.53819   
Dmoz_Computers_keyphrase3_GAT     0.21713  0.458008  0.500303  0.564616   
Dmoz_Computers_keyphrase23_GCN   0.181494  0.439143  0.499953  0.541133   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.060083   0.16327  0.262413  0.389853   
Industry_Sector_keyphrase3_GCN   0.069709  0.135784  0.225724  0.225994   
Industry_Sector_keyphrase3_GAT   0.074275  0.180922  0.301666  0.386414   
Industry_Sector_keyphrase23_GCN  0.065985  0.130461  0.203032  0.287367   
Industry_Sector_keyphrase23_GAT  0.057123  0.181028  0.308498  0.412669   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.514408  NaN  0.478176  
Dmoz_Computers_keyphrase2_GAT     0.53552  NaN  0.519144  
Dmoz_Computers_keyphrase3_GCN     0.54316  NaN  0.380957  
Dmoz_Computers_keyphrase3_GAT    0.567121  NaN  0.419065  
Dmoz_Computers_keyphrase23_GCN   0.555106  NaN  0.123545  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.303421  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.111563  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.416675  NaN       NaN  
Industry_Sector_keyphrase23_GCN   0.35434  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.424404  NaN       NaN  

[72 rows x 7 columns]

time: 27 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[1][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.211999  0.390988  0.482557  0.510626   
Dmoz_Computers_keyphrase2_GAT    0.253935  0.438995  0.485262  0.522026   
Dmoz_Computers_keyphrase3_GCN     0.25148  0.430334  0.509801  0.545159   
Dmoz_Computers_keyphrase3_GAT     0.28474  0.454366  0.534224   0.54675   
Dmoz_Computers_keyphrase23_GCN   0.277317  0.383824  0.512913   0.54395   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT    0.09299  0.181284  0.289442  0.387363   
Industry_Sector_keyphrase3_GCN   0.039973  0.128949  0.071315  0.063629   
Industry_Sector_keyphrase3_GAT   0.094086  0.172188   0.29629  0.394508   
Industry_Sector_keyphrase23_GCN  0.077443  0.142706  0.178674  0.097033   
Industry_Sector_keyphrase23_GAT  0.084933   0.19342  0.304612  0.384316   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.515384  NaN  0.409276  
Dmoz_Computers_keyphrase2_GAT    0.541415  NaN  0.462330  
Dmoz_Computers_keyphrase3_GCN    0.558557  NaN  0.262949  
Dmoz_Computers_keyphrase3_GAT    0.580489  NaN  0.311605  
Dmoz_Computers_keyphrase23_GCN   0.535998  NaN  0.038043  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.415581  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.284316  NaN       NaN  
Industry_Sector_keyphrase3_GAT    0.41006  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.294588  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.421863  NaN       NaN  

[72 rows x 7 columns]

time: 27 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[2][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.199056  0.421254  0.473944    0.4907   
Dmoz_Computers_keyphrase2_GAT     0.26292  0.435277  0.489124  0.514551   
Dmoz_Computers_keyphrase3_GCN    0.233437  0.462878  0.516498  0.547552   
Dmoz_Computers_keyphrase3_GAT    0.302879  0.472139  0.507227  0.550349   
Dmoz_Computers_keyphrase23_GCN   0.204991  0.406814  0.512639  0.536758   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.058068  0.126668  0.300286   0.35871   
Industry_Sector_keyphrase3_GCN   0.083456  0.119522  0.224641  0.238213   
Industry_Sector_keyphrase3_GAT   0.048064  0.181907  0.285887  0.376387   
Industry_Sector_keyphrase23_GCN  0.036144  0.153257  0.094945  0.273865   
Industry_Sector_keyphrase23_GAT  0.052514  0.181762   0.31454   0.39262   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.512357  NaN  0.495991  
Dmoz_Computers_keyphrase2_GAT    0.538309  NaN  0.508564  
Dmoz_Computers_keyphrase3_GCN    0.563477  NaN  0.386309  
Dmoz_Computers_keyphrase3_GAT    0.572761  NaN  0.425171  
Dmoz_Computers_keyphrase23_GCN   0.562281  NaN  0.124373  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT    0.43135  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.290718  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.392771  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.120149  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.443086  NaN       NaN  

[72 rows x 7 columns]

time: 27.5 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[3][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.162363  0.412142  0.449561  0.491876   
Dmoz_Computers_keyphrase2_GAT    0.231033  0.430254  0.467741  0.511945   
Dmoz_Computers_keyphrase3_GCN    0.232027  0.448604  0.495864  0.544154   
Dmoz_Computers_keyphrase3_GAT    0.275318  0.448801  0.508095  0.549106   
Dmoz_Computers_keyphrase23_GCN   0.174267  0.441876  0.499012  0.518209   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.066235  0.222089  0.278688  0.386097   
Industry_Sector_keyphrase3_GCN   0.057041  0.169316  0.204632  0.060473   
Industry_Sector_keyphrase3_GAT   0.075842  0.223092  0.273152  0.400501   
Industry_Sector_keyphrase23_GCN   0.05475  0.174732  0.228741  0.019846   
Industry_Sector_keyphrase23_GAT  0.067324  0.222253   0.25882  0.382315   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.513443  NaN  0.459047  
Dmoz_Computers_keyphrase2_GAT    0.539705  NaN  0.474102  
Dmoz_Computers_keyphrase3_GCN    0.562193  NaN  0.250482  
Dmoz_Computers_keyphrase3_GAT    0.585424  NaN  0.284558  
Dmoz_Computers_keyphrase23_GCN   0.552792  NaN  0.073177  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.372298  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.066733  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.410404  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.047246  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.403717  NaN       NaN  

[72 rows x 7 columns]

time: 28.8 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[4][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.160871  0.404689  0.454942  0.513054   
Dmoz_Computers_keyphrase2_GAT    0.203635  0.432552  0.492477   0.53046   
Dmoz_Computers_keyphrase3_GCN    0.166201  0.427966  0.503038  0.546662   
Dmoz_Computers_keyphrase3_GAT    0.231284  0.468893  0.529411  0.549777   
Dmoz_Computers_keyphrase23_GCN   0.177913  0.448857  0.501754  0.533646   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.064603  0.191011  0.296518  0.366261   
Industry_Sector_keyphrase3_GCN   0.062269  0.152671  0.124721  0.128798   
Industry_Sector_keyphrase3_GAT    0.08031  0.215915  0.342436  0.399354   
Industry_Sector_keyphrase23_GCN  0.035495  0.167808   0.28666  0.043886   
Industry_Sector_keyphrase23_GAT  0.068884  0.209497  0.343207  0.399842   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.525567  NaN  0.148378  
Dmoz_Computers_keyphrase2_GAT    0.525563  NaN  0.514830  
Dmoz_Computers_keyphrase3_GCN    0.552323  NaN  0.360900  
Dmoz_Computers_keyphrase3_GAT    0.577275  NaN  0.383843  
Dmoz_Computers_keyphrase23_GCN   0.542522  NaN  0.113919  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.419533  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.311646  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.449447  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.086533  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.413612  NaN       NaN  

[72 rows x 7 columns]

time: 25.5 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[5][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.207538  0.409182  0.445336  0.495257   
Dmoz_Computers_keyphrase2_GAT     0.18834  0.443953  0.470605  0.513515   
Dmoz_Computers_keyphrase3_GCN    0.183499  0.461187  0.484169  0.529759   
Dmoz_Computers_keyphrase3_GAT    0.189712  0.478295  0.491244   0.54332   
Dmoz_Computers_keyphrase23_GCN   0.179754  0.445262  0.477305  0.527307   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.084585  0.233129  0.313509  0.376535   
Industry_Sector_keyphrase3_GCN   0.042792  0.171052   0.24271  0.037548   
Industry_Sector_keyphrase3_GAT   0.060753  0.201925   0.32035   0.39997   
Industry_Sector_keyphrase23_GCN  0.045068  0.142127  0.237279  0.096213   
Industry_Sector_keyphrase23_GAT    0.0623  0.214003  0.282992   0.39983   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN       0.508  NaN  0.456996  
Dmoz_Computers_keyphrase2_GAT    0.532389  NaN  0.455886  
Dmoz_Computers_keyphrase3_GCN    0.544974  NaN  0.328744  
Dmoz_Computers_keyphrase3_GAT    0.555907  NaN  0.354366  
Dmoz_Computers_keyphrase23_GCN   0.530813  NaN  0.049196  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.309835  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.071785  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.432291  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.350394  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.418168  NaN       NaN  

[72 rows x 7 columns]

time: 23.8 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[6][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.191212  0.417282  0.475036  0.499117   
Dmoz_Computers_keyphrase2_GAT    0.237159  0.457832  0.491795  0.520929   
Dmoz_Computers_keyphrase3_GCN    0.181069  0.441315  0.518482  0.536009   
Dmoz_Computers_keyphrase3_GAT    0.258256  0.461657  0.522197  0.550133   
Dmoz_Computers_keyphrase23_GCN   0.200668  0.454391  0.497118   0.53622   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.087467  0.211964  0.286228  0.390847   
Industry_Sector_keyphrase3_GCN   0.090941  0.189515  0.210131  0.322002   
Industry_Sector_keyphrase3_GAT   0.142412  0.257271  0.308864  0.429405   
Industry_Sector_keyphrase23_GCN  0.124889  0.148901  0.058335  0.341462   
Industry_Sector_keyphrase23_GAT  0.137938  0.240311  0.322024  0.403318   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.518824  NaN  0.422209  
Dmoz_Computers_keyphrase2_GAT    0.540569  NaN  0.457992  
Dmoz_Computers_keyphrase3_GCN    0.567367  NaN  0.326300  
Dmoz_Computers_keyphrase3_GAT    0.574345  NaN  0.341452  
Dmoz_Computers_keyphrase23_GCN   0.548881  NaN  0.039363  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.402086  NaN       NaN  
Industry_Sector_keyphrase3_GCN     0.3267  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.395699  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.114086  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.428539  NaN       NaN  

[72 rows x 7 columns]

time: 26.3 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[7][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN     0.19525  0.385943   0.44143  0.505576   
Dmoz_Computers_keyphrase2_GAT     0.20564  0.421712  0.466294  0.523154   
Dmoz_Computers_keyphrase3_GCN     0.23208  0.441194  0.505355  0.532262   
Dmoz_Computers_keyphrase3_GAT    0.240836   0.46238  0.509329  0.543059   
Dmoz_Computers_keyphrase23_GCN   0.174567  0.429403  0.489388  0.536563   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT    0.06414  0.181742  0.229923  0.388929   
Industry_Sector_keyphrase3_GCN   0.041986  0.203847  0.264162  0.187748   
Industry_Sector_keyphrase3_GAT   0.057616  0.244275  0.321453    0.4142   
Industry_Sector_keyphrase23_GCN  0.071175  0.151134  0.223547  0.157212   
Industry_Sector_keyphrase23_GAT  0.057599  0.232876  0.296509  0.413507   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.505937  NaN  0.454261  
Dmoz_Computers_keyphrase2_GAT    0.517087  NaN  0.471486  
Dmoz_Computers_keyphrase3_GCN    0.556456  NaN  0.219853  
Dmoz_Computers_keyphrase3_GAT    0.565164  NaN  0.294505  
Dmoz_Computers_keyphrase23_GCN   0.543464  NaN  0.049093  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.397736  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.332114  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.434276  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.058785  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.438996  NaN       NaN  

[72 rows x 7 columns]

time: 30.8 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[8][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN     0.15254  0.387944  0.461129  0.479802   
Dmoz_Computers_keyphrase2_GAT    0.204015  0.440646  0.498881  0.508576   
Dmoz_Computers_keyphrase3_GCN     0.18602  0.456378  0.520907  0.537207   
Dmoz_Computers_keyphrase3_GAT    0.234128   0.46544   0.52285  0.531966   
Dmoz_Computers_keyphrase23_GCN   0.209099  0.455507  0.515185   0.52259   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.077434  0.232485  0.300552  0.377055   
Industry_Sector_keyphrase3_GCN   0.081521  0.170551  0.250238  0.113671   
Industry_Sector_keyphrase3_GAT   0.078476  0.242809  0.315856  0.369923   
Industry_Sector_keyphrase23_GCN  0.034276  0.148286   0.21686  0.259441   
Industry_Sector_keyphrase23_GAT  0.055349  0.268406  0.316138  0.378918   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.503758  NaN  0.443082  
Dmoz_Computers_keyphrase2_GAT    0.535902  NaN  0.447280  
Dmoz_Computers_keyphrase3_GCN    0.541505  NaN  0.250930  
Dmoz_Computers_keyphrase3_GAT    0.562081  NaN  0.244450  
Dmoz_Computers_keyphrase23_GCN   0.533721  NaN  0.026772  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.418951  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.335374  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.430665  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.073537  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.436439  NaN       NaN  

[72 rows x 7 columns]

time: 23.7 ms (started: 2024-09-09 23:34:14 +00:00)


In [ ]:
df_list[9][3]

1         5        10        20  \
Dmoz_Computers_keyphrase2_GCN    0.160313  0.394329  0.458341  0.484051   
Dmoz_Computers_keyphrase2_GAT    0.201082  0.434988  0.490078  0.496693   
Dmoz_Computers_keyphrase3_GCN    0.131783  0.418329  0.530608  0.516547   
Dmoz_Computers_keyphrase3_GAT    0.213011  0.448801  0.538233  0.534771   
Dmoz_Computers_keyphrase23_GCN   0.194119  0.395052  0.512874  0.514895   
...                                   ...       ...       ...       ...   
Industry_Sector_keyphrase2_GAT   0.073497  0.238746  0.307874  0.275164   
Industry_Sector_keyphrase3_GCN   0.067655  0.163816  0.217986  0.276372   
Industry_Sector_keyphrase3_GAT   0.093388  0.235167  0.321181  0.401388   
Industry_Sector_keyphrase23_GCN  0.043592  0.141217  0.225023  0.227121   
Industry_Sector_keyphrase23_GAT  0.090788  0.246185  0.354782  0.392233   

                                       30  80%        80  
Dmoz_Computers_keyphrase2_GCN    0.521699  NaN  0.454998  
Dmoz_Computers_keyphrase2_GAT    0.539747  NaN  0.480132  
Dmoz_Computers_keyphrase3_GCN    0.552399  NaN  0.263597  
Dmoz_Computers_keyphrase3_GAT    0.561372  NaN  0.288204  
Dmoz_Computers_keyphrase23_GCN   0.539947  NaN  0.123754  
...                                   ...  ...       ...  
Industry_Sector_keyphrase2_GAT   0.373511  NaN       NaN  
Industry_Sector_keyphrase3_GCN   0.128291  NaN       NaN  
Industry_Sector_keyphrase3_GAT   0.422489  NaN       NaN  
Industry_Sector_keyphrase23_GCN  0.130231  NaN       NaN  
Industry_Sector_keyphrase23_GAT  0.407573  NaN       NaN  

[72 rows x 7 columns]

time: 24.5 ms (started: 2024-09-09 23:34:14 +00:00)
